In [1]:
import sys
import os
from os import path
root_path = path.dirname(path.abspath(os.path.abspath('')))
print(root_path)
sys.path.append(root_path)
from speech.utils import misc
from speech.utils import objects
from speech.utils import vad as vad_api
from speech.emotion import emotion_api as emotion_api
import librosa
import numpy as np
import pandas as pd
import os
from keras.models import model_from_json
import jsonpickle
import shutil
from flask import Flask
from flask import request
import time
import tensorflow as tf
import webrtcvad
import IPython.display as ipd

/home/absin/Documents/dev/ai


Using TensorFlow backend.


In [2]:
loaded_model = emotion_api.getModel()
loaded_model._make_predict_function()

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


/home/absin/Documents/dev/ai/speech/utils/constants.py:13: YAMLLoadWarning: calling yaml.load() without Loader=... is deprecated, as the default Loader is unsafe. Please read https://msg.pyyaml.org/load for full details.
  doc = yaml.load(f)


Loaded model and weights from disk


In [3]:
url = 'https://storage.googleapis.com/istar-static/17975929.wav'

In [4]:
folder = '/home/absin/Downloads/'
f = misc.download_file(url, folder)

Successfully downloaded 17975929.wav from url: https://storage.googleapis.com/istar-static/17975929.wav to folder: /home/absin/Downloads/


In [5]:
f

{'abs_path': '/home/absin/Downloads/17975929.wav', 'success': True}

In [6]:
X, sample_rate = librosa.load(f['abs_path'], res_type='kaiser_fast', sr=22050*2, offset=0)
sample_rate = np.array(sample_rate)

In [7]:
X.shape

(5780276,)

In [8]:
num_samples = X.shape[0]
time = num_samples / (44100)
time
chunk_duration  = 2.5
chunk_window = 0.5
chunk_frames = int(44100 * chunk_duration)
chunk_window_frames = int(44100 * chunk_window)
# We need to collect samples every 2.5 second window and jump by say 0.5 seconds
# In order to do this we will take 2.5* 44100 from the X and make it into a vector then pass it to the model

In [9]:

#aggressiveness = 3
#vad = webrtcvad.Vad(aggressiveness)
#X11, sample_rate11 = librosa.load(f['abs_path'], res_type='kaiser_fast', sr=16000, offset=0)
down_sampled = folder + '123.wav'
misc.stereo_to_mono(f['abs_path'], down_sampled)
X11, sample_rate11, audio_length = vad_api.read_wave(down_sampled)

In [10]:
sample_rate11

8000

In [18]:
def is_valid_chunk(chunks):
    aggressiveness = 3
    vad = webrtcvad.Vad(aggressiveness)
    yes_count = 0
    no_count = 0
    frame_dur_ms = 20
    window_chunks = int(frame_dur_ms*sample_rate11/1000)
    curr_ind = 0.0
    has_more = (len(chunks)>window_chunks)
    from_time = 0.0
    to_time = frame_dur_ms/1000
    while(has_more):
        vad_input = chunks[int(curr_ind):int(curr_ind+window_chunks)]
        assert webrtcvad.valid_rate_and_frame_length(sample_rate11, len(vad_input))
        try:
            is_speech = vad.is_speech(vad_input, sample_rate11)
        except Exception as e:
            print(e)
            is_speech = False
        if is_speech:
            yes_count += 1
        else:
            no_count += 1
        print('{} - {} : {}'.format(from_time, to_time, is_speech))
        curr_ind += window_chunks
        from_time += frame_dur_ms/1000
        to_time += frame_dur_ms/1000
        has_more = (len(chunks)>curr_ind)
    print('{} : {}'.format(yes_count, no_count))
    if ((yes_count*100/(yes_count + no_count)) > 80):
        return True
    else:
        return False

In [19]:
curr_index = 0
from_time = 0.0
to_time = 2.5
has_elements = (len(X)>chunk_frames)
while(has_elements):
    chunk = X[curr_index:(curr_index+chunk_frames)]
    mfccs = np.mean(librosa.feature.mfcc(
        y=chunk, sr=sample_rate, n_mfcc=13), axis=0)
    featurelive = mfccs
    livedf2 = featurelive
    livedf2 = pd.DataFrame(data=livedf2)
    livedf2 = livedf2.stack().to_frame().T
    twodim = np.expand_dims(livedf2, axis=2)
    livepreds = loaded_model.predict(twodim,batch_size=32,verbose=1)
    livepreds1 = livepreds.argmax(axis=1)
    labels = ['female_angry', 'female_calm', 'female_fearful', 'female_happy',
              'female_sad', 'male_angry', 'male_calm', 'male_fearful', 'male_happy', 'male_sad']
    ppp = labels[livepreds1[0]] + str(livepreds[0][livepreds1[0]])
    if is_valid_chunk(X11[int(from_time*sample_rate11):int(to_time*sample_rate11)]):
        if livepreds[0][livepreds1[0]] > 0.85:
            print('{} -- {} ---> {}'.format(from_time, to_time, ppp))
        else:
            print('{} -- {} ---> Invalid'.format(from_time, to_time))
    
    curr_index += chunk_window_frames
    from_time+=chunk_window
    to_time+=chunk_window
    has_elements = ((curr_index + chunk_frames) < len(X))

1/1 [==============================] - 0s 2ms/step
0.0 - 0.02 : False
0.02 - 0.04 : False
0.04 - 0.06 : False
0.06 - 0.08 : False
0.08 - 0.1 : False
0.1 - 0.12000000000000001 : False
0.12000000000000001 - 0.14 : False
0.14 - 0.16 : False
0.16 - 0.18 : False
0.18 - 0.19999999999999998 : False
0.19999999999999998 - 0.21999999999999997 : False
0.21999999999999997 - 0.23999999999999996 : False
0.23999999999999996 - 0.25999999999999995 : False
0.25999999999999995 - 0.27999999999999997 : False
0.27999999999999997 - 0.3 : False
0.3 - 0.32 : False
0.32 - 0.34 : False
0.34 - 0.36000000000000004 : False
0.36000000000000004 - 0.38000000000000006 : False
0.38000000000000006 - 0.4000000000000001 : False
0.4000000000000001 - 0.4200000000000001 : False
0.4200000000000001 - 0.4400000000000001 : False
0.4400000000000001 - 0.46000000000000013 : False
0.46000000000000013 - 0.48000000000000015 : False
0.48000000000000015 - 0.5000000000000001 : False
0.5000000000000001 - 0.5200000000000001 : False
0.520000

0.0 - 0.02 : False
0.02 - 0.04 : False
0.04 - 0.06 : False
0.06 - 0.08 : False
0.08 - 0.1 : False
0.1 - 0.12000000000000001 : False
0.12000000000000001 - 0.14 : False
0.14 - 0.16 : False
0.16 - 0.18 : False
0.18 - 0.19999999999999998 : False
0.19999999999999998 - 0.21999999999999997 : False
0.21999999999999997 - 0.23999999999999996 : False
0.23999999999999996 - 0.25999999999999995 : False
0.25999999999999995 - 0.27999999999999997 : False
0.27999999999999997 - 0.3 : False
0.3 - 0.32 : False
0.32 - 0.34 : False
0.34 - 0.36000000000000004 : False
0.36000000000000004 - 0.38000000000000006 : False
0.38000000000000006 - 0.4000000000000001 : False
0.4000000000000001 - 0.4200000000000001 : False
0.4200000000000001 - 0.4400000000000001 : False
0.4400000000000001 - 0.46000000000000013 : False
0.46000000000000013 - 0.48000000000000015 : False
0.48000000000000015 - 0.5000000000000001 : False
0.5000000000000001 - 0.5200000000000001 : False
0.5200000000000001 - 0.5400000000000001 : False
0.540000000

0.0 - 0.02 : False
0.02 - 0.04 : False
0.04 - 0.06 : False
0.06 - 0.08 : False
0.08 - 0.1 : False
0.1 - 0.12000000000000001 : False
0.12000000000000001 - 0.14 : False
0.14 - 0.16 : False
0.16 - 0.18 : False
0.18 - 0.19999999999999998 : False
0.19999999999999998 - 0.21999999999999997 : False
0.21999999999999997 - 0.23999999999999996 : False
0.23999999999999996 - 0.25999999999999995 : False
0.25999999999999995 - 0.27999999999999997 : False
0.27999999999999997 - 0.3 : False
0.3 - 0.32 : False
0.32 - 0.34 : False
0.34 - 0.36000000000000004 : False
0.36000000000000004 - 0.38000000000000006 : False
0.38000000000000006 - 0.4000000000000001 : False
0.4000000000000001 - 0.4200000000000001 : False
0.4200000000000001 - 0.4400000000000001 : False
0.4400000000000001 - 0.46000000000000013 : False
0.46000000000000013 - 0.48000000000000015 : False
0.48000000000000015 - 0.5000000000000001 : False
0.5000000000000001 - 0.5200000000000001 : False
0.5200000000000001 - 0.5400000000000001 : False
0.540000000

0.0 - 0.02 : False
0.02 - 0.04 : False
0.04 - 0.06 : False
0.06 - 0.08 : False
0.08 - 0.1 : False
0.1 - 0.12000000000000001 : False
0.12000000000000001 - 0.14 : False
0.14 - 0.16 : False
0.16 - 0.18 : False
0.18 - 0.19999999999999998 : False
0.19999999999999998 - 0.21999999999999997 : False
0.21999999999999997 - 0.23999999999999996 : False
0.23999999999999996 - 0.25999999999999995 : False
0.25999999999999995 - 0.27999999999999997 : False
0.27999999999999997 - 0.3 : False
0.3 - 0.32 : False
0.32 - 0.34 : False
0.34 - 0.36000000000000004 : False
0.36000000000000004 - 0.38000000000000006 : False
0.38000000000000006 - 0.4000000000000001 : False
0.4000000000000001 - 0.4200000000000001 : False
0.4200000000000001 - 0.4400000000000001 : False
0.4400000000000001 - 0.46000000000000013 : False
0.46000000000000013 - 0.48000000000000015 : False
0.48000000000000015 - 0.5000000000000001 : False
0.5000000000000001 - 0.5200000000000001 : False
0.5200000000000001 - 0.5400000000000001 : False
0.540000000

1/1 [==============================] - 0s 2ms/step
0.0 - 0.02 : False
0.02 - 0.04 : False
0.04 - 0.06 : False
0.06 - 0.08 : False
0.08 - 0.1 : False
0.1 - 0.12000000000000001 : False
0.12000000000000001 - 0.14 : False
0.14 - 0.16 : False
0.16 - 0.18 : False
0.18 - 0.19999999999999998 : False
0.19999999999999998 - 0.21999999999999997 : False
0.21999999999999997 - 0.23999999999999996 : False
0.23999999999999996 - 0.25999999999999995 : False
0.25999999999999995 - 0.27999999999999997 : False
0.27999999999999997 - 0.3 : False
0.3 - 0.32 : False
0.32 - 0.34 : False
0.34 - 0.36000000000000004 : False
0.36000000000000004 - 0.38000000000000006 : False
0.38000000000000006 - 0.4000000000000001 : False
0.4000000000000001 - 0.4200000000000001 : False
0.4200000000000001 - 0.4400000000000001 : False
0.4400000000000001 - 0.46000000000000013 : False
0.46000000000000013 - 0.48000000000000015 : False
0.48000000000000015 - 0.5000000000000001 : False
0.5000000000000001 - 0.5200000000000001 : False
0.520000

...

1/1 [==============================] - 0s 2ms/step
0.0 - 0.02 : True
0.02 - 0.04 : True
0.04 - 0.06 : True
0.06 - 0.08 : True
0.08 - 0.1 : True
0.1 - 0.12000000000000001 : True
0.12000000000000001 - 0.14 : True
0.14 - 0.16 : True
0.16 - 0.18 : True
0.18 - 0.19999999999999998 : True
0.19999999999999998 - 0.21999999999999997 : True
0.21999999999999997 - 0.23999999999999996 : True
0.23999999999999996 - 0.25999999999999995 : True
0.25999999999999995 - 0.27999999999999997 : True
0.27999999999999997 - 0.3 : True
0.3 - 0.32 : True
0.32 - 0.34 : True
0.34 - 0.36000000000000004 : True
0.36000000000000004 - 0.38000000000000006 : True
0.38000000000000006 - 0.4000000000000001 : True
0.4000000000000001 - 0.4200000000000001 : True
0.4200000000000001 - 0.4400000000000001 : True
0.4400000000000001 - 0.46000000000000013 : True
0.46000000000000013 - 0.48000000000000015 : False
0.48000000000000015 - 0.5000000000000001 : False
0.5000000000000001 - 0.5200000000000001 : False
0.5200000000000001 - 0.54000000

1/1 [==============================] - 0s 2ms/step
0.0 - 0.02 : True
0.02 - 0.04 : True
0.04 - 0.06 : True
0.06 - 0.08 : True
0.08 - 0.1 : True
0.1 - 0.12000000000000001 : True
0.12000000000000001 - 0.14 : True
0.14 - 0.16 : False
0.16 - 0.18 : False
0.18 - 0.19999999999999998 : False
0.19999999999999998 - 0.21999999999999997 : True
0.21999999999999997 - 0.23999999999999996 : True
0.23999999999999996 - 0.25999999999999995 : True
0.25999999999999995 - 0.27999999999999997 : True
0.27999999999999997 - 0.3 : True
0.3 - 0.32 : True
0.32 - 0.34 : True
0.34 - 0.36000000000000004 : True
0.36000000000000004 - 0.38000000000000006 : True
0.38000000000000006 - 0.4000000000000001 : True
0.4000000000000001 - 0.4200000000000001 : True
0.4200000000000001 - 0.4400000000000001 : True
0.4400000000000001 - 0.46000000000000013 : True
0.46000000000000013 - 0.48000000000000015 : True
0.48000000000000015 - 0.5000000000000001 : True
0.5000000000000001 - 0.5200000000000001 : True
0.5200000000000001 - 0.54000000

1/1 [==============================] - 0s 2ms/step
0.0 - 0.02 : False
0.02 - 0.04 : False
0.04 - 0.06 : False
0.06 - 0.08 : False
0.08 - 0.1 : False
0.1 - 0.12000000000000001 : False
0.12000000000000001 - 0.14 : False
0.14 - 0.16 : False
0.16 - 0.18 : False
0.18 - 0.19999999999999998 : False
0.19999999999999998 - 0.21999999999999997 : False
0.21999999999999997 - 0.23999999999999996 : False
0.23999999999999996 - 0.25999999999999995 : False
0.25999999999999995 - 0.27999999999999997 : False
0.27999999999999997 - 0.3 : False
0.3 - 0.32 : False
0.32 - 0.34 : False
0.34 - 0.36000000000000004 : False
0.36000000000000004 - 0.38000000000000006 : False
0.38000000000000006 - 0.4000000000000001 : False
0.4000000000000001 - 0.4200000000000001 : False
0.4200000000000001 - 0.4400000000000001 : False
0.4400000000000001 - 0.46000000000000013 : False
0.46000000000000013 - 0.48000000000000015 : False
0.48000000000000015 - 0.5000000000000001 : False
0.5000000000000001 - 0.5200000000000001 : False
0.520000

1/1 [==============================] - 0s 2ms/step
0.0 - 0.02 : True
0.02 - 0.04 : True
0.04 - 0.06 : True
0.06 - 0.08 : True
0.08 - 0.1 : True
0.1 - 0.12000000000000001 : True
0.12000000000000001 - 0.14 : True
0.14 - 0.16 : True
0.16 - 0.18 : True
0.18 - 0.19999999999999998 : True
0.19999999999999998 - 0.21999999999999997 : True
0.21999999999999997 - 0.23999999999999996 : True
0.23999999999999996 - 0.25999999999999995 : True
0.25999999999999995 - 0.27999999999999997 : True
0.27999999999999997 - 0.3 : True
0.3 - 0.32 : True
0.32 - 0.34 : True
0.34 - 0.36000000000000004 : True
0.36000000000000004 - 0.38000000000000006 : True
0.38000000000000006 - 0.4000000000000001 : True
0.4000000000000001 - 0.4200000000000001 : True
0.4200000000000001 - 0.4400000000000001 : True
0.4400000000000001 - 0.46000000000000013 : True
0.46000000000000013 - 0.48000000000000015 : True
0.48000000000000015 - 0.5000000000000001 : True
0.5000000000000001 - 0.5200000000000001 : True
0.5200000000000001 - 0.54000000000

1/1 [==============================] - 0s 2ms/step
0.0 - 0.02 : True
0.02 - 0.04 : True
0.04 - 0.06 : True
0.06 - 0.08 : True
0.08 - 0.1 : True
0.1 - 0.12000000000000001 : True
0.12000000000000001 - 0.14 : True
0.14 - 0.16 : True
0.16 - 0.18 : True
0.18 - 0.19999999999999998 : True
0.19999999999999998 - 0.21999999999999997 : True
0.21999999999999997 - 0.23999999999999996 : True
0.23999999999999996 - 0.25999999999999995 : True
0.25999999999999995 - 0.27999999999999997 : True
0.27999999999999997 - 0.3 : True
0.3 - 0.32 : True
0.32 - 0.34 : True
0.34 - 0.36000000000000004 : True
0.36000000000000004 - 0.38000000000000006 : True
0.38000000000000006 - 0.4000000000000001 : True
0.4000000000000001 - 0.4200000000000001 : True
0.4200000000000001 - 0.4400000000000001 : True
0.4400000000000001 - 0.46000000000000013 : True
0.46000000000000013 - 0.48000000000000015 : True
0.48000000000000015 - 0.5000000000000001 : True
0.5000000000000001 - 0.5200000000000001 : True
0.5200000000000001 - 0.54000000000

In [20]:
start = 6.5
end = start + 2.5
ipd.Audio(X[int(start*44100): int(end*44100)], rate = 44100) # load a chunk of raw audio

In [21]:
start = 6.5
end = start + 2.5
is_valid_chunk(X11[int(start*sample_rate11):int(end*sample_rate11)])

0.0 - 0.02 : True
0.02 - 0.04 : True
0.04 - 0.06 : True
0.06 - 0.08 : True
0.08 - 0.1 : True
0.1 - 0.12000000000000001 : True
0.12000000000000001 - 0.14 : True
0.14 - 0.16 : True
0.16 - 0.18 : True
0.18 - 0.19999999999999998 : True
0.19999999999999998 - 0.21999999999999997 : True
0.21999999999999997 - 0.23999999999999996 : True
0.23999999999999996 - 0.25999999999999995 : True
0.25999999999999995 - 0.27999999999999997 : True
0.27999999999999997 - 0.3 : True
0.3 - 0.32 : True
0.32 - 0.34 : True
0.34 - 0.36000000000000004 : True
0.36000000000000004 - 0.38000000000000006 : True
0.38000000000000006 - 0.4000000000000001 : True
0.4000000000000001 - 0.4200000000000001 : True
0.4200000000000001 - 0.4400000000000001 : True
0.4400000000000001 - 0.46000000000000013 : True
0.46000000000000013 - 0.48000000000000015 : True
0.48000000000000015 - 0.5000000000000001 : True
0.5000000000000001 - 0.5200000000000001 : True
0.5200000000000001 - 0.5400000000000001 : True
0.5400000000000001 - 0.560000000000000

True

In [16]:
ipd.Audio(f['abs_path'])  # load a local WAV file